### 练习4. Agent API 服务

#### 目标
1. 使用FastAPI公开Agent的SSE接口
2. 使用一个简单的客户端模拟用户来调用这个SSE

#### 要求
1. 练习2中的收集信息的AI 通过 Agno实现，可以和用户进行流式对话
2. 通过FastAPI SSE 协议输出Agent Stream Response
    - https://github.com/agno-agi/agent-api 
3. 脚本运行在控制台，可以实现打字机效果的信息收集
    - AI 的输出应该和deepseek 一样，是打字机效果


In [1]:
import os
from dotenv import load_dotenv

load_dotenv()
base_url = os.getenv('BAILIAN_API_BASE_URL')
api_key = os.getenv('BAILIAN_API_KEY')

In [5]:
from agno.agent import Agent
from agno.tools import tool
from agno.memory.v2.db.sqlite import SqliteMemoryDb
from agno.memory.v2.memory import Memory
from agno.storage.sqlite import SqliteStorage
from agno.models.openai.like import OpenAILike
from typing import Optional, Dict, Any
from enum import Enum
import json

SYSTEM_PROMPT = """
    你是一个信息收集助手。你需要依次收集用户的姓名、年龄和感兴趣的行业。
    如果用户输入其他无关内容，请提醒用户需要先完成信息收集。
    开始对话前，请先介绍自己。
    
    工具使用规则：
    1. 每当用户提供有效信息时，必须立即使用 add_info 工具保存信息
    2. 使用 get_info 工具检查特定信息是否已收集
    3. 使用 list_info 工具确认所有已收集的信息

    信息收集策略：
    1. 使用开放式问题引导用户提供更多信息
    2. 对模糊的信息进行澄清和确认
    3. 根据上下文，智能地推断和补充相关信息
    4. 保持对话的自然性和连贯性
    5. 务必保证信息的准确性和完整性
    6. 只有当信息符合需要收集的内容的规则时（例如姓名必须是符合姓名规则的，年龄必须是1~100内的数字等等），才将其记录到已收集信息中
    7. 如果用户输入年龄时给出的是出生年份，请帮用户计算实际年龄（今年是2025年）。
    8. 如果用户输入的年龄没有明确的数字，则此输入无效。

    对话要求：
    1. 保持友好、专业的语调
    2. 每次回复要简洁明了
    3. 每个信息收集成功后，确认用户输入的内容，格式为："好的，已经收集到您的(此处为收集的项目)是："，并询问下一个问题。
    4. 当用户询问一些其他问题时，请礼貱地告诉用户，你是一个信息收集助手，不回答其它不相关问题。提醒用户还没收集完成。
    5. 所有问题回答并收集完毕后，请务必要总结用户的所有信息，并告知用户"信息已收集完毕"。
    6. 如果没有对话历史，请先介绍自己，再进行询问。
    7. 如果用户回答与问题无关，请礼貌且友好地提醒用户需要回答相关问题。
    8. 请不要直接将问题内容直接输出，而是要根据用户的回答进行智能化的处理和回复。

    注意事项：
    除非用户输入与信息收集无关，否则一定要调用对应的tools再给予回复。
    除非用户输入与信息收集无关，否则一定要调用对应的tools再给予回复。
    除非用户输入与信息收集无关，否则一定要调用对应的tools再给予回复。
    除非用户输入与信息收集无关，否则一定要调用对应的tools再给予回复。
    除非用户输入与信息收集无关，否则一定要调用对应的tools再给予回复。
    除非用户输入与信息收集无关，否则一定要调用对应的tools再给予回复。
"""

# 初始化空的session状态
initial_state = {
    "name": None,
    "age": None,
    "industry": None
}

class DataField(str, Enum):
    NAME = "name"
    AGE = "age"
    INDUSTRY = "industry"

@tool(name="add_info", description="添加或修改用户信息")
def add_info(agent: Agent, field: DataField, value: str) -> str:
    if field == DataField.NAME:
        agent.session_state["name"] = value
        return json.dumps({"result": f"已收集姓名: {value}"})
    elif field == DataField.AGE:
        try:
            age = int(value)
            agent.session_state["age"] = age
            return json.dumps({"result": f"已收集年龄: {age}"})
        except ValueError:
            return json.dumps({"result": "年龄输入无效，请输入一个正确的数字。"})
    elif field == DataField.INDUSTRY:
        agent.session_state["industry"] = value
        return json.dumps({"result": f"已收集感兴趣的行业: {value}"})

@tool(name="get_info", description="获取用户信息")
def get_info(agent:Agent, field: DataField) -> str:
    info = agent.session_state.get(field)
    if info is None:
        info = "未收集" if field != DataField.AGE else "未收集"
    return json.dumps({"result": str(info)})

@tool(name="list_info", description="列出所有用户信息")
def list_info(agent:Agent) -> str:
    user_info = agent.session_state
    info = {
        "姓名": user_info.get("name") or "未收集",
        "年龄": user_info.get("age") or "未收集",
        "感兴趣的行业": user_info.get("industry") or "未收集"
    }
    return json.dumps({"result": info})

# 配置
user_id = "test"
session_id = "325"
db_file = "tmp/agent.db"

# 模型配置
model = OpenAILike(
    id="qwen3-32b",
    api_key=api_key,
    base_url=base_url,
    request_params={
        "extra_body": {"enable_thinking": False},
        # "response_format": {"type": "json_object"}
    },
)

# 初始化内存和存储
memory = Memory(
    model=model,
    db=SqliteMemoryDb(table_name="user_memories", db_file=db_file),
)
storage = SqliteStorage(table_name="agent_sessions", db_file=db_file)

# 创建agent实例
agent = Agent(
    model=model,
    tools=[add_info, get_info, list_info],
    instructions=SYSTEM_PROMPT,
    add_datetime_to_instructions=True,
    show_tool_calls=True,
    markdown=True,
    memory=memory,
    enable_user_memories=True,
    storage=storage,
    add_history_to_messages=True,
    enable_session_summaries=True,
    session_state=initial_state,
    add_state_in_messages=True,
    session_id=session_id,
)

In [6]:
# 主对话循环
agent.print_response("你好", stream=True, user_id=user_id)
while True:
    user_input = input("用户: ")
    if user_input.lower() in ['exit', 'quit']:
        print("对话结束。")
        break
    if not user_input.strip():
        print("输入不能为空，请重新输入。")
        continue

    agent.print_response(""+user_input, stream=True, user_id=user_id)

Output()

ERROR    API status error from OpenAI API: Error code: 400 - {'error': {'code': 'invalid_parameter_error', 'param':
         None, 'message': "<400> InternalError.Algo.InvalidParameter: 'messages' must contain the word 'json' in   
         some form, to use 'response_format' of type 'json_object'.", 'type': 'invalid_request_error'}, 'id':      
         'chatcmpl-1e479ee3-9537-9c96-a975-f7636f971412', 'request_id': '1e479ee3-9537-9c96-a975-f7636f971412'}

WARNING  Error in memory/summary operation: <400> InternalError.Algo.InvalidParameter: 'messages' must contain the 
         word 'json' in some form, to use 'response_format' of type 'json_object'.

Output()

ERROR    API status error from OpenAI API: Error code: 400 - {'error': {'code': 'invalid_parameter_error', 'param':
         None, 'message': "<400> InternalError.Algo.InvalidParameter: 'messages' must contain the word 'json' in   
         some form, to use 'response_format' of type 'json_object'.", 'type': 'invalid_request_error'}, 'id':      
         'chatcmpl-10940767-691f-94db-ae9b-22cecb594092', 'request_id': '10940767-691f-94db-ae9b-22cecb594092'}

...

WARNING  Error in memory/summary operation: <400> InternalError.Algo.InvalidParameter: 'messages' must contain the 
         word 'json' in some form, to use 'response_format' of type 'json_object'.

Output()

ERROR    API status error from OpenAI API: Error code: 400 - {'error': {'code': 'invalid_parameter_error', 'param':
         None, 'message': "<400> InternalError.Algo.InvalidParameter: 'messages' must contain the word 'json' in   
         some form, to use 'response_format' of type 'json_object'.", 'type': 'invalid_request_error'}, 'id':      
         'chatcmpl-e66c74dc-790f-97ec-8fe7-92317f6ead7b', 'request_id': 'e66c74dc-790f-97ec-8fe7-92317f6ead7b'}

WARNING  Error in memory/summary operation: <400> InternalError.Algo.InvalidParameter: 'messages' must contain the 
         word 'json' in some form, to use 'response_format' of type 'json_object'.

对话结束。
